In [ ]:
!pip3 install kaggle

In [ ]:
!mkdir .kaggle

In [ ]:
!mkdir ~/.kaggle
!touch .kaggle/kaggle.json

In [ ]:
import json
token={"username":"farazg","key":"b5be7130eafb77e0096caa86fec3d14c"}
with open('/root/.kaggle/kaggle.json','w') as file:
    json.dump(token, file)

!chmod 600 ~/.kaggle/kaggle.json

!kaggle datasets download -d srbhshinde/flickr8k-sau
    

100% 2.07G/2.08G [01:02<00:00, 38.9MB/s]
100% 2.08G/2.08G [01:02<00:00, 35.6MB/s]


In [ ]:
ls


flickr8k-sau.zip  glove.6B.50d.txt  sample_data/


In [ ]:
!unzip flickr8k-sau.zip

Streaming output truncated to the last 5000 lines.
  inflating: flickr8k-sau/Flickr_Data/Images/2844747252_64567cf14a.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2844846111_8c1cbfc75d.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2844963839_ff09cdb81f.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2845246160_d0d1bbd6f0.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2845691057_d4ab89d889.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2845845721_d0bc113ff7.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2846037553_1a1de50709.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2846785268_904c5fcf9f.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2846843520_b0e6211478.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2847514745_9a35493023.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2847615962_c330bded6e.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2847859796_4d9cb0d31f.jpg  
  inflating: flickr8k-sau/Flickr_Data/Images/2848266893_9693c66275.jpg  


In [ ]:
ls


flickr8k-sau/  flickr8k-sau.zip  Flickr_Data/  glove.6B.50d.txt  sample_data/


In [ ]:
import pandas as pd
import numpy as  np
import matplotlib.pyplot as plt
import keras
import re
import nltk 
from nltk.corpus import stopwords

import string
import json
from time import time
import pickle
from keras.applications.vgg16 import VGG16
from keras.applications.resnet import ResNet50, preprocess_input,decode_predictions
from keras.preprocessing import image
from keras.models import Model,load_model
from keras.preprocessing.sequence import pad_sequences

from keras.layers import Input, Dense, Dropout,Embedding,LSTM

from keras.layers.merge import add
from tensorflow.keras.utils import to_categorical

In [ ]:
cd Flickr_Data/

/content/Flickr_Data


In [ ]:
ls

Flickr_TextData/  Images/


In [ ]:
cd ..

/content


In [ ]:
fliker_path='/content/Flickr_Data/'


In [ ]:
with open(fliker_path+"Flickr_TextData/Flickr8k.token.txt") as filepath:
  caption=filepath.read()
  filepath.close()

In [ ]:
captions= caption.split("\n")[:-1]

In [ ]:
len(captions)

40460

In [ ]:
captions[:5]

['1000268201_693b08cb0e.jpg#0\tA child in a pink dress is climbing up a set of stairs in an entry way .',
 '1000268201_693b08cb0e.jpg#1\tA girl going into a wooden building .',
 '1000268201_693b08cb0e.jpg#2\tA little girl climbing into a wooden playhouse .',
 '1000268201_693b08cb0e.jpg#3\tA little girl climbing the stairs to her playhouse .',
 '1000268201_693b08cb0e.jpg#4\tA little girl in a pink dress going into a wooden cabin .']

In [ ]:
dicti={}

for i in captions:
     captions_da=i.split("\t")
     image_name=captions_da[0].split(".")[0]
     captions_data=captions_da[1]

     if dicti.get(image_name) == None:
          dicti[image_name]=[]
   
     dicti[image_name].append(captions_data)

In [ ]:
dicti["1000268201_693b08cb0e"]

['A child in a pink dress is climbing up a set of stairs in an entry way .',
 'A girl going into a wooden building .',
 'A little girl climbing into a wooden playhouse .',
 'A little girl climbing the stairs to her playhouse .',
 'A little girl in a pink dress going into a wooden cabin .']

In [ ]:
#cleaning the data 


def data_clean(caption):
    caption= caption.lower()
    caption= re.sub("[^a-z]+"," ",caption)
    caption= caption.split()
    caption= [x for x in caption if len(x)>1]
    caption =" ".join(caption)
    return caption

In [ ]:
test_data="xvnoizhdnsdoha&5svndklvakcavak;vnadpvjddvm;dvoadjvdAABSBD"
result=data_clean(test_data)
print(result)

xvnoizhdnsdoha svndklvakcavak vnadpvjddvm dvoadjvdaabsbd


In [ ]:
for keys,values in dicti.items():
  for  i  in range(0,len(values)):
        values[i]=data_clean(values[i])

for keys,values in dicti.items():
       for i in range(0,len(values)):
            print(values[i])       

Streaming output truncated to the last 5000 lines.
dog is jumping over log in wooded area while carrying another log
dog with stick in his mouth jumps over fallen tree in the forest
dog carries stick and jumps over log
the dog carries stick and jumps over log in the woods
the dog jumps over the log with stick in its mouth
black and brown dog is running between two cement barriers with snow
dog runs down the cold aisle
black and tan small dog walking with perked ears
the black and brown dog walks toward the camera in an enclosed snowy area
the brown and black dog is running through snowy street
furry dog is running through doorway leading to plants
furry tan dog is outside on patio
short furry dog stands on brick floor in front of group of potted plants
very hairy dog is running down hall
flowers are behind the fluffy dog that is coming up the step
brown and black dog runs through the leaves
brown dog is running
brown dog with red collar jumping across leafy lawn
dog with brindle colore

In [ ]:
dicti["1000268201_693b08cb0e"]

['child in pink dress is climbing up set of stairs in an entry way',
 'girl going into wooden building',
 'little girl climbing into wooden playhouse',
 'little girl climbing the stairs to her playhouse',
 'little girl in pink dress going into wooden cabin']

In [ ]:
clean_file=open("dicti.txt","w")
clean_file.write(str(dicti))
clean_file.close()

In [ ]:
cleaned_data=open("dicti.txt",'r')
clear_data=cleaned_data.read()
cleaned_data.close()



In [ ]:
clear_data

"{'1000268201_693b08cb0e': ['child in pink dress is climbing up set of stairs in an entry way', 'girl going into wooden building', 'little girl climbing into wooden playhouse', 'little girl climbing the stairs to her playhouse', 'little girl in pink dress going into wooden cabin'], '1001773457_577c3a7d70': ['black dog and spotted dog are fighting', 'black dog and tri colored dog playing with each other on the road', 'black dog and white dog with brown spots are staring at each other in the street', 'two dogs of different breeds looking at each other on the road', 'two dogs on pavement moving toward each other'], '1002674143_1b742ab4b8': ['little girl covered in paint sits in front of painted rainbow with her hands in bowl', 'little girl is sitting in front of large painted rainbow', 'small girl in the grass plays with fingerpaints in front of white canvas with rainbow on it', 'there is girl with pigtails sitting in front of rainbow painting', 'young girl with pigtails painting outside 

In [ ]:
unique_vocabulary = set()

for key in dicti.keys():
      for x in dicti[key]:
         unique_vocabulary.update(x.split())
print("vocabularay size:%d" % len(unique_vocabulary))

vocabularay size:8424


In [ ]:
total_vocabularies=[]


for lis in dicti.keys():
   for dic in dicti[keys]:
      for x in dic.split():
          total_vocabularies.append(x)

print("length:",len(total_vocabularies))
print(total_vocabularies[:3000])


length: 315588
['man', 'in', 'pink', 'shirt', 'climbs', 'rock', 'face', 'man', 'is', 'rock', 'climbing', 'high', 'in', 'the', 'air', 'person', 'in', 'red', 'shirt', 'climbing', 'up', 'rock', 'face', 'covered', 'in', 'assist', 'handles', 'rock', 'climber', 'in', 'red', 'shirt', 'rock', 'climber', 'practices', 'on', 'rock', 'climbing', 'wall', 'man', 'in', 'pink', 'shirt', 'climbs', 'rock', 'face', 'man', 'is', 'rock', 'climbing', 'high', 'in', 'the', 'air', 'person', 'in', 'red', 'shirt', 'climbing', 'up', 'rock', 'face', 'covered', 'in', 'assist', 'handles', 'rock', 'climber', 'in', 'red', 'shirt', 'rock', 'climber', 'practices', 'on', 'rock', 'climbing', 'wall', 'man', 'in', 'pink', 'shirt', 'climbs', 'rock', 'face', 'man', 'is', 'rock', 'climbing', 'high', 'in', 'the', 'air', 'person', 'in', 'red', 'shirt', 'climbing', 'up', 'rock', 'face', 'covered', 'in', 'assist', 'handles', 'rock', 'climber', 'in', 'red', 'shirt', 'rock', 'climber', 'practices', 'on', 'rock', 'climbing', 'wall', 

In [ ]:
import collections

counting= collections.Counter(total_vocabularies)
count_of_words=dict(counting)

print(count_of_words)
print(len(count_of_words))

{'man': 16184, 'in': 40460, 'pink': 8092, 'shirt': 24276, 'climbs': 8092, 'rock': 48552, 'face': 16184, 'is': 8092, 'climbing': 24276, 'high': 8092, 'the': 8092, 'air': 8092, 'person': 8092, 'red': 16184, 'up': 8092, 'covered': 8092, 'assist': 8092, 'handles': 8092, 'climber': 16184, 'practices': 8092, 'on': 8092, 'wall': 8092}
22


In [ ]:


sorted_data = sorted(count_of_words.items(),reverse=True,key=lambda x:x[1])
print(sorted_data)
len(sorted_data)

[('rock', 48552), ('in', 40460), ('shirt', 24276), ('climbing', 24276), ('man', 16184), ('face', 16184), ('red', 16184), ('climber', 16184), ('pink', 8092), ('climbs', 8092), ('is', 8092), ('high', 8092), ('the', 8092), ('air', 8092), ('person', 8092), ('up', 8092), ('covered', 8092), ('assist', 8092), ('handles', 8092), ('practices', 8092), ('on', 8092), ('wall', 8092)]


22

In [ ]:
threshold_value=5

vocab= [x for x in sorted_data if x[1]>threshold_value]
print(vocab)
len(vocab)

[('rock', 48552), ('in', 40460), ('shirt', 24276), ('climbing', 24276), ('man', 16184), ('face', 16184), ('red', 16184), ('climber', 16184), ('pink', 8092), ('climbs', 8092), ('is', 8092), ('high', 8092), ('the', 8092), ('air', 8092), ('person', 8092), ('up', 8092), ('covered', 8092), ('assist', 8092), ('handles', 8092), ('practices', 8092), ('on', 8092), ('wall', 8092)]


22

In [ ]:
final_vocab_list=[x[0] for x in vocab]
print(final_vocab_list)
len(final_vocab_list)

['rock', 'in', 'shirt', 'climbing', 'man', 'face', 'red', 'climber', 'pink', 'climbs', 'is', 'high', 'the', 'air', 'person', 'up', 'covered', 'assist', 'handles', 'practices', 'on', 'wall']


22

In [ ]:
#prep imagetraining data


traning_data=open("/content/flickr8k-sau/Flickr_Data/Flickr_TextData/Flickr_8k.trainImages.txt")
train=traning_data.read()
traning_data.close()

print(train)
len(train)






2513260012_03d33305cf.jpg
2903617548_d3e38d7f88.jpg
3338291921_fe7ae0c8f8.jpg
488416045_1c6d903fe0.jpg
2644326817_8f45080b87.jpg
218342358_1755a9cce1.jpg
2501968935_02f2cd8079.jpg
2699342860_5288e203ea.jpg
2638369467_8fc251595b.jpg
2926786902_815a99a154.jpg
2851304910_b5721199bc.jpg
3423802527_94bd2b23b0.jpg
3356369156_074750c6cc.jpg
2294598473_40637b5c04.jpg
1191338263_a4fa073154.jpg
2380765956_6313d8cae3.jpg
3197891333_b1b0fd1702.jpg
3119887967_271a097464.jpg
2276499757_b44dc6f8ce.jpg
2506892928_7e79bec613.jpg
2187222896_c206d63396.jpg
2826769554_85c90864c9.jpg
3097196395_ec06075389.jpg
3603116579_4a28a932e2.jpg
3339263085_6db9fd0981.jpg
2532262109_87429a2cae.jpg
2076906555_c20dc082db.jpg
2502007071_82a8c639cf.jpg
3113769557_9edbb8275c.jpg
3325974730_3ee192e4ff.jpg
1655781989_b15ab4cbff.jpg
1662261486_db967930de.jpg
2410562803_56ec09f41c.jpg
2469498117_b4543e1460.jpg
69710415_5c2bfb1058.jpg
3414734842_beb543f400.jpg
3006217970_90b42e6b27.jpg
2192411521_9c7e488c5e.jpg
3535879138_9281d

154678

In [ ]:
train=[x.split(".")[0] for x in train.split("\n")[:-1]]
train

['2513260012_03d33305cf',
 '2903617548_d3e38d7f88',
 '3338291921_fe7ae0c8f8',
 '488416045_1c6d903fe0',
 '2644326817_8f45080b87',
 '218342358_1755a9cce1',
 '2501968935_02f2cd8079',
 '2699342860_5288e203ea',
 '2638369467_8fc251595b',
 '2926786902_815a99a154',
 '2851304910_b5721199bc',
 '3423802527_94bd2b23b0',
 '3356369156_074750c6cc',
 '2294598473_40637b5c04',
 '1191338263_a4fa073154',
 '2380765956_6313d8cae3',
 '3197891333_b1b0fd1702',
 '3119887967_271a097464',
 '2276499757_b44dc6f8ce',
 '2506892928_7e79bec613',
 '2187222896_c206d63396',
 '2826769554_85c90864c9',
 '3097196395_ec06075389',
 '3603116579_4a28a932e2',
 '3339263085_6db9fd0981',
 '2532262109_87429a2cae',
 '2076906555_c20dc082db',
 '2502007071_82a8c639cf',
 '3113769557_9edbb8275c',
 '3325974730_3ee192e4ff',
 '1655781989_b15ab4cbff',
 '1662261486_db967930de',
 '2410562803_56ec09f41c',
 '2469498117_b4543e1460',
 '69710415_5c2bfb1058',
 '3414734842_beb543f400',
 '3006217970_90b42e6b27',
 '2192411521_9c7e488c5e',
 '3535879138_928

In [ ]:
testing_data=open("/content/flickr8k-sau/Flickr_Data/Flickr_TextData/Flickr_8k.testImages.txt")
test_data=testing_data.read()
testing_data.close()

print(test_data)

3385593926_d3e9c21170.jpg
2677656448_6b7e7702af.jpg
311146855_0b65fdb169.jpg
1258913059_07c613f7ff.jpg
241347760_d44c8d3a01.jpg
2654514044_a70a6e2c21.jpg
2339106348_2df90aa6a9.jpg
256085101_2c2617c5d0.jpg
280706862_14c30d734a.jpg
3072172967_630e9c69d0.jpg
3482062809_3b694322c4.jpg
1167669558_87a8a467d6.jpg
2847615962_c330bded6e.jpg
3344233740_c010378da7.jpg
2435685480_a79d42e564.jpg
3110649716_c17e14670e.jpg
2511019188_ca71775f2d.jpg
2521770311_3086ca90de.jpg
2723477522_d89f5ac62b.jpg
2218609886_892dcd6915.jpg
3745451546_fc8ec70cbd.jpg
2844018783_524b08e5aa.jpg
3100251515_c68027cc22.jpg
2207244634_1db1a1890b.jpg
2943023421_e297f05e11.jpg
3286822339_5535af6b93.jpg
2479652566_8f9fac8af5.jpg
1394368714_3bc7c19969.jpg
872622575_ba1d3632cc.jpg
2309860995_c2e2a0feeb.jpg
241347204_007d83e252.jpg
3502343542_f9b46688e5.jpg
757332692_6866ae545c.jpg
2748729903_3c7c920c4d.jpg
494792770_2c5f767ac0.jpg
3213992947_3f3f967a9f.jpg
2295750198_6d152d7ceb.jpg
2358898017_24496b80e8.jpg
3222055946_45f7293bb

In [ ]:
test=[x.split(".")[0] for x in test_data.split("\n")[:-1]]
print(test)

['3385593926_d3e9c21170', '2677656448_6b7e7702af', '311146855_0b65fdb169', '1258913059_07c613f7ff', '241347760_d44c8d3a01', '2654514044_a70a6e2c21', '2339106348_2df90aa6a9', '256085101_2c2617c5d0', '280706862_14c30d734a', '3072172967_630e9c69d0', '3482062809_3b694322c4', '1167669558_87a8a467d6', '2847615962_c330bded6e', '3344233740_c010378da7', '2435685480_a79d42e564', '3110649716_c17e14670e', '2511019188_ca71775f2d', '2521770311_3086ca90de', '2723477522_d89f5ac62b', '2218609886_892dcd6915', '3745451546_fc8ec70cbd', '2844018783_524b08e5aa', '3100251515_c68027cc22', '2207244634_1db1a1890b', '2943023421_e297f05e11', '3286822339_5535af6b93', '2479652566_8f9fac8af5', '1394368714_3bc7c19969', '872622575_ba1d3632cc', '2309860995_c2e2a0feeb', '241347204_007d83e252', '3502343542_f9b46688e5', '757332692_6866ae545c', '2748729903_3c7c920c4d', '494792770_2c5f767ac0', '3213992947_3f3f967a9f', '2295750198_6d152d7ceb', '2358898017_24496b80e8', '3222055946_45f7293bb2', '444481722_690d0cadcf', '2647049

In [ ]:
train_dicti={}

print(train[0])
for i in train:
  train_dicti[i]=[]
  for x in dicti[i]:
   final_cap="<starting of the sequence>"+ x +"<ending of  the sequence>"
   train_dicti[i].append(final_cap)


2513260012_03d33305cf


In [ ]:
train_dicti["2513260012_03d33305cf"]

['<starting of the sequence>black dog is running after white dog in the snow<ending of  the sequence>',
 '<starting of the sequence>black dog chasing brown dog through snow<ending of  the sequence>',
 '<starting of the sequence>two dogs chase each other across the snowy ground<ending of  the sequence>',
 '<starting of the sequence>two dogs play together in the snow<ending of  the sequence>',
 '<starting of the sequence>two dogs running through low lying body of water<ending of  the sequence>']

In [ ]:
train_dicti['1000268201_693b08cb0e']

['<starting of the sequence>child in pink dress is climbing up set of stairs in an entry way<ending of  the sequence>',
 '<starting of the sequence>girl going into wooden building<ending of  the sequence>',
 '<starting of the sequence>little girl climbing into wooden playhouse<ending of  the sequence>',
 '<starting of the sequence>little girl climbing the stairs to her playhouse<ending of  the sequence>',
 '<starting of the sequence>little girl in pink dress going into wooden cabin<ending of  the sequence>']

In [ ]:
img="/content/flickr8k-sau/Flickr_Data/Images"
print(img)

/content/flickr8k-sau/Flickr_Data/Images


In [ ]:
mymodel=ResNet50(weights="imagenet",input_shape=(224,224,3))

102981632/102967424 [==============================] - 1s 0us/step


In [ ]:
mymodel.summary()

Model: "resnet50"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 224, 224, 3  0           []                               
                                )]                                                                
                                                                                                  
 conv1_pad (ZeroPadding2D)      (None, 230, 230, 3)  0           ['input_1[0][0]']                
                                                                                                  
 conv1_conv (Conv2D)            (None, 112, 112, 64  9472        ['conv1_pad[0][0]']              
                                )                                                                 
                                                                                           

In [ ]:
new_model=Model(mymodel.input,mymodel.layers[-2].output)

In [ ]:
new_model.summary()

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 224, 224, 3  0           []                               
                                )]                                                                
                                                                                                  
 conv1_pad (ZeroPadding2D)      (None, 230, 230, 3)  0           ['input_1[0][0]']                
                                                                                                  
 conv1_conv (Conv2D)            (None, 112, 112, 64  9472        ['conv1_pad[0][0]']              
                                )                                                                 
                                                                                              

In [ ]:
def preprocess_image(img):
  img=image.load_img(img,target_size=(224,224))
  img=image.img_to_array(img)
  img=np.expand_dims(img,axis=0)
  img=preprocess_input(img)
  return img


In [ ]:
def encoding_images(img):
  images=preprocess_image(img)
  featured_vector=new_model.predict(images)
  featured_vector=featured_vector.reshape(featured_vector.shape[1],)
  return featured_vector

In [ ]:
for key, values in train_dicti.items():
    print(values)

Streaming output truncated to the last 5000 lines.
['<starting of the sequence>the couple eat their meal outside<ending of  the sequence>', '<starting of the sequence>two people sit on bench<ending of  the sequence>', '<starting of the sequence>two people sitting facing away with dreadlocks<ending of  the sequence>', '<starting of the sequence>two people with dreadlocks<ending of  the sequence>', '<starting of the sequence>two people with dreadlocks sit on wooden bench<ending of  the sequence>']
['<starting of the sequence>boy and girl playing cricket<ending of  the sequence>', '<starting of the sequence>boy and yellow and girl in red playing cricket<ending of  the sequence>', '<starting of the sequence>girl in red top bowls cricket ball at boy in yellow shirt who is in front of the wicket holding bat<ending of  the sequence>', '<starting of the sequence>young boy and girl playing baseball in grassy field<ending of  the sequence>', '<starting of the sequence>two young children playing 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
encode_train={}


for x ,y in enumerate(train):
  y="/content/Flickr_Data/Images/{}.jpg".format(train[x])
  encode_train[y]= encoding_images(y)
  if x%100==0:
    print("encoded images:"+str(x))


encoded images:0
encoded images:100
encoded images:200
encoded images:300
encoded images:400
encoded images:500
encoded images:600
encoded images:700
encoded images:800
encoded images:900
encoded images:1000
encoded images:1100
encoded images:1200
encoded images:1300
encoded images:1400
encoded images:1500
encoded images:1600
encoded images:1700
encoded images:1800
encoded images:1900
encoded images:2000
encoded images:2100
encoded images:2200
encoded images:2300
encoded images:2400
encoded images:2500
encoded images:2600
encoded images:2700
encoded images:2800
encoded images:2900
encoded images:3000
encoded images:3100
encoded images:3200
encoded images:3300
encoded images:3400
encoded images:3500
encoded images:3600
encoded images:3700
encoded images:3800
encoded images:3900
encoded images:4000
encoded images:4100
encoded images:4200
encoded images:4300
encoded images:4400
encoded images:4500
encoded images:4600
encoded images:4700
encoded images:4800
encoded images:4900
encoded imag

In [ ]:
with open("/encoded_train_images.pkl","wb") as encode_pickle:
  pickle.dump(encode_train,encode_pickle)

In [ ]:
mode_path="/content/Flickr_Data/Images/"
encode_train[mode_path+"111766423_4522d36e56.jpg"]


array([0.2145782 , 0.0010708 , 0.9212484 , ..., 0.25015894, 0.06509534,
       0.        ], dtype=float32)

In [ ]:
encode_test={}


for x ,y in enumerate(test):
  y="/content/flickr8k-sau/Flickr_Data/Images/{}.jpg".format(test[x])
  encode_test[y[len(img):]]= encoding_images(y)

  if x%100==0:
    print("encoded images:",str(x))


encoded images: 0
encoded images: 100
encoded images: 200
encoded images: 300
encoded images: 400
encoded images: 500
encoded images: 600
encoded images: 700
encoded images: 800
encoded images: 900


In [ ]:
with open("/encoded_test_images.pkl","wb") as encode1_pickle:
  pickle.dump(encode_test,encode1_pickle)

In [ ]:
with open("/encoded_train_images.pkl","rb") as encode_pickle:
  encode_train=pickle.load(encode_pickle)

In [ ]:
with open("/encoded_test_images.pkl","rb") as encode1_pickle:
  encode_test=pickle.load(encode1_pickle)

In [ ]:

x=1
index_to_word={}
word_to_index={}

for i in final_vocab_list:
  word_to_index[i]=x
  index_to_word[x]=i
  x=x+1

In [ ]:
word_to_index['shirt']

3

In [ ]:
index_to_word[3]

'shirt'

In [ ]:
word_to_index["<starting of the sequence>"]=23
word_to_index["<ending of  the sequence>"]=24

In [ ]:
word_to_index['<ending of  the sequence>']

24

In [ ]:
index_to_word[23]="<starting of the sequence>"
index_to_word[24]="<ending of  the sequence>"

In [ ]:
vocab_size=len(index_to_word)+2
voc=len(word_to_index)+2
print(vocab_size)

24


In [ ]:
length_of_captions=[]


for key in train_dicti.keys():
   for x in train_dicti[key]:
     length_of_captions.append(len(x.split()))




In [ ]:
print(length_of_captions)

[16, 13, 15, 13, 15, 10, 13, 14, 17, 19, 18, 14, 15, 19, 16, 12, 15, 14, 12, 18, 17, 12, 14, 10, 15, 15, 17, 15, 22, 18, 20, 16, 18, 19, 21, 14, 11, 11, 19, 19, 10, 20, 14, 17, 12, 15, 17, 22, 15, 22, 11, 14, 14, 16, 21, 12, 13, 8, 14, 15, 16, 10, 12, 15, 13, 11, 9, 13, 12, 19, 14, 15, 17, 11, 21, 18, 16, 18, 17, 17, 22, 16, 14, 12, 15, 13, 22, 21, 21, 21, 16, 16, 17, 19, 14, 13, 16, 12, 11, 14, 22, 20, 20, 14, 17, 18, 23, 14, 22, 25, 12, 12, 9, 19, 12, 16, 20, 15, 9, 14, 15, 16, 17, 18, 11, 26, 17, 18, 12, 10, 20, 21, 16, 17, 24, 13, 22, 20, 16, 18, 20, 21, 19, 19, 21, 16, 10, 15, 14, 14, 10, 17, 17, 17, 12, 17, 16, 16, 13, 10, 17, 15, 11, 15, 16, 11, 21, 12, 18, 14, 18, 17, 13, 16, 20, 17, 20, 13, 14, 14, 17, 14, 17, 16, 16, 17, 15, 20, 16, 20, 16, 16, 18, 20, 12, 21, 14, 17, 14, 13, 14, 23, 14, 11, 21, 12, 16, 14, 13, 13, 16, 17, 14, 13, 11, 11, 9, 11, 12, 12, 12, 19, 18, 17, 19, 18, 19, 21, 12, 18, 14, 20, 11, 12, 11, 14, 13, 13, 16, 16, 16, 18, 17, 15, 16, 17, 13, 14, 16, 18, 11, 

In [ ]:
MAX_LEN=max(length_of_captions)
print(MAX_LEN)

39


In [ ]:
for key, values in train_dicti.items():
           photo=encode_train[mode_path+key+".jpg"]
           print(photo)
           for x in values:
                 print(x)

Streaming output truncated to the last 5000 lines.
<starting of the sequence>person is eating pasta while dog is watching<ending of  the sequence>
<starting of the sequence>someone in blue and white striped sweater is eating and the dog next to them is interested in their food<ending of  the sequence>
[0.02735292 0.8034104  0.24806657 ... 3.2092013  0.2867026  0.12857762]
<starting of the sequence>camera team wearing jackets stands in front of white building<ending of  the sequence>
<starting of the sequence>man is setting up camera to take shots of something that ca be seen near zchtv wall<ending of  the sequence>
<starting of the sequence>man shoots footage with camera as two women look on<ending of  the sequence>
<starting of the sequence>man with long hair is looking through camera<ending of  the sequence>
<starting of the sequence>three people stand outside one has camera on tripod<ending of  the sequence>
[0.05535315 0.         0.25236526 ... 3.6711478  0.33235058 0.0365812 ]
<st

In [ ]:


def generator(train_dicti,encode_train,word_to_index,MAX_LEN,number_of_pictures_per_bath):
    n_samples = 0
    
    X= []
    y_in = []
    y_out = []
    
    while True:
        
       for key, values in train_dicti.items():
           n_samples=n_samples+1
           photo=encode_train[mode_path+key+".jpg"]
           for x in values:
                 seq=[word_to_index[word] for word in x.split() if word in word_to_index]
                 for i in range(1, len(seq)):

                     in_seq= [seqeuence[0:i]]
                     out_seq = seq[i]

                     in_seq = pad_sequences([in_seq], maxlen=MAX_LEN,value=0, padding='post')[0]
                     out_seq = to_categorical([out_seq], num_classes=vocab_size)[0]
                     X.append(photo)
                     y_in.append(in_seq)
                     y_out.append(out_seq)
            
    return X, y_in, y_out

    if n_samples==number_of_pictures_per_bath:
       yield[[np.array(X),np.array(y_in)],np.array( y_out)]
       X= []
       y_in = []
       y_out = []
       n_samples=0

In [ ]:
f=open("/content/glove.6B.50d.txt",encoding="utf8")
f

<_io.TextIOWrapper name='/content/glove.6B.50d.txt' mode='r' encoding='utf8'>

In [ ]:
embeddings_index = dict()
fid = open('glove.6B.50d.txt',encoding="utf8")
for line in fid:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:],dtype='float32')
    embeddings_index[word] = coefs
fid.close()

In [ ]:
def embedding_output():
   e_dim=50
   emb_output=np.zeros((vocab_size,e_dim))

   for x,y in word_to_index.items():
     embedding_vector=embedding_ind.get(x)

     if embedding_vector is not None:
          emb_output[y]=embedding_vector

   return emb_output


   
embedding_output=embedding_output()

In [ ]:
embedding_output

array([[ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [-0.64670002,  0.98997998, -0.14379001, ..., -1.22590005,
        -0.79443002, -0.4614    ],
       [ 0.33041999,  0.24995001, -0.60873997, ..., -0.50703001,
        -0.027273  , -0.53285003],
       ...,
       [ 0.30045   ,  0.25005999, -0.16692001, ..., -0.07131   ,
         0.23052   , -0.51938999],
       [ 0.26381999,  0.32453001,  0.74185002, ..., -0.77772999,
         0.16744   , -0.81748998],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ]])

In [ ]:
embedding_output.shape

(24, 50)

In [ ]:
inputs1 = Input(shape=(2048,))
image_feature = Dropout(0.5)(inputs1)
image_feature = Dense(256, activation='relu')(image_feature)
    # sequence model
inputs2 = Input(shape=(MAX_LEN,))
language_feature = Embedding(vocab_size,50, weights=[embedding_output],input_length=MAX_LEN, trainable=False)(inputs2)
    #Embedding(vocab_size, 256, mask_zero=True)(inputs2) #<<<<<< fix me, add pretrianed embedding
language_feature = Dropout(0.3)(language_feature)
language_feature = LSTM(256)(language_feature)
    # decoder model
output = add([image_feature, language_feature])
output = Dense(256, activation='relu')(output)
output = Dense(vocab_size, activation='softmax')(output)
    # tie it together [image, seq] [word]
model = Model(inputs=[inputs1, inputs2], outputs=output)
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['acc'])
    # summarize model
print(model.summary())


Model: "model_1"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_3 (InputLayer)           [(None, 39)]         0           []                               
                                                                                                  
 input_2 (InputLayer)           [(None, 2048)]       0           []                               
                                                                                                  
 embedding (Embedding)          (None, 39, 50)       1200        ['input_3[0][0]']                
                                                                                                  
 dropout (Dropout)              (None, 2048)         0           ['input_2[0][0]']                
                                                                                            

In [ ]:
epochs=20
number_of_pictures_per_bath=3
steps=len(train_dicti)
steps

6000

In [ ]:
for i in range(epochs):
  gen=generator(train_dicti,encode_train,MAX_LEN,word_to_index,number_of_pictures_per_bath)
  model.fit_generator(gen,epochs=1,steps_per_epoch=steps,verbose=1)
  model.save("./model_"+str(i)+".h5")

In [ ]:
model=load_model("./model_19.h5")

In [ ]:


def predicting_caption(img):
  adding_start="<starting of the sequence>"

  for i in range(MAX_LEN):
    sequence=[word_to_index[x] for x in adding_start.split() if x in word_to_index]
    sequence=pad_sequences([sequence],maxlen=MAX_LEN,padding="post")

    yprediction=model.predict([photo,sequence])
    yprediction=yprediction.argmax()
    word=index_to_word[yprediction]
    adding_start+=" "+word
    
    if word=="<end of the seqeuence>":
       break
    final_caption=adding_start.split()
    final_caption=final_caption[1:-1]
    final_caption=" ".join(final_caption) 

    return final_caption 

In [ ]:
for i in range(20):
  reimg=np.random.randint(0,1000)
  imgg_name=list(encode_test.keys())[reimg]
  fin_photo=encode_test[imgg_name].reshape((1,2048))


  i=plt.imread(img+imgg_name)
  plt.imshow(i)
  plt.axis("off")
  plt.show()


  final=predicting_caption(fin_photo)
  print(final)
  

In [ ]:
pip install gTTS

In [ ]:
from gtts import gTTS
  
# This module is imported so that we can 
# play the converted audio
import os
  
# The text that you want to convert to audio
mytext =text
  
# Language in which you want to convert
language = 'en'
  
# Passing the text and language to the engine, 
# here we have marked slow=False. Which tells 
# the module that the converted audio should 
# have a high speed
myobj = gTTS(text=mytext, lang=language, slow=False)
  
# Saving the converted audio in a mp3 file named
# welcome 
myobj.save("introoooooo.mp3")
  
# Playing the converted file
os.system("mpg321 intro.mp3")